# GridWorld example

This notebook serves as an example of a typical (perhaps *the most* typical) problem that search algorithms are used to solve. It is basically an abstract "Google maps" problem, or how to move a character in a video game.

Disclaimer: the code is *not* meant to be super optimised or otherwise polished, but to convey the message and to be easily read.

The "world" (problem) is represented by a class GridWorld. Remember, for the application of a search algorithm, we need to define the following methods: Solved to check whether the current position is the goal node or not, GenerateMoves to find successors of the current state (where can we go from here) -- this implicitly defines our state space, Move/UndoMove to procees to the successor state or backtrack from it, and the __ init __ that basically sets up the starting state. Additionally, for heuristic search, we need to define the Evaluate method to heuristically assess how good the given position is.

The other methods are not strictly required, but are helpful.

In [1]:
from random import random

In [12]:
class GridWorld:
    def __init__(self, Rows = 20, Columns = 20, ObstacleProb = 0.3):
        self.GridHeight = Rows                  # number of rows in the grid
        self.GridWidth = Columns                # number of columns in the grid
        self.ObstacleProb = ObstacleProb        # probability of a square being an obstacle
        self.Grid = self.GenerateGridWorld()
        
        # start and goal position in the grid (as a complex number)
        self.State = 2 + 2j 
        self.Goal = self.GridHeight - 5 + (self.GridWidth - 5) * 1j

        # store the starting position
        self.StartingPosition = (self.State, self.Goal, self.Grid)

    def GenerateGridWorld(self):
        grid = [int(random() < self.ObstacleProb) for n in range(self.GridHeight * self.GridWidth)]
        grid[2 * self.GridHeight + 2] = 0
        grid[(self.GridHeight - 5) * self.GridWidth + self.GridWidth - 5] = 0
        return grid

    def SetStandardPosition(self):
        # sets a standard gridworld position for use in classroom
        self.GridHeight = 10
        self.GridWidth = 10
        self.ObstacleProb = 0.3
        self.Grid = [ 0,0,0,0,0,0,0,1,1,1,
                      1,1,1,0,1,0,0,1,0,0,
                      1,0,0,0,1,0,0,1,0,1,
                      0,0,1,0,0,0,1,1,1,1,
                      1,0,0,0,0,1,1,0,0,1,
                      1,1,0,1,1,0,0,1,0,0,
                      1,0,0,0,1,0,0,0,0,0,
                      1,0,0,0,1,0,0,0,0,0,
                      0,0,0,0,0,0,0,0,0,0,
                      0,0,0,0,1,1,0,0,0,0 ]
        self.State = 2 + 2j
        self.Goal = self.GridHeight - 5 + (self.GridWidth - 5) * 1j
        self.StartingPosition = (self.State, self.Goal, self.Grid)
        
    def ID(self):
        # ID is simply the same as State (single complex number)
        return self.State

    def ResetPosition(self):
        self.State, self.Goal, self.Grid = self.StartingPosition

    def PrintPosition(self):
        for c in range(self.GridWidth*3 + 4): print('=', end='')
        print()
        for r in range(self.GridHeight):
            print('||', end=''),
            for c in range(self.GridWidth):
                if r + c * 1j == self.Goal: print(' O ', end='')
                elif r + c * 1j == self.State: print(' X ', end='')
                elif self.Grid[r * self.GridWidth + c]: print('###', end='')
                else: print('   ', end='')
            print('||')
        for c in range(self.GridWidth*3 + 4): print('=', end='')
        print()

    def ExecuteSequence(self, sequence):
        for m in sequence:
            self.Move(m)

    def UndoSequence(self, sequence):
        for m in reversed(sequence):
            self.UndoMove(m)
    
    def Move(self, move_and_cost):
        move, cost = move_and_cost
        self.State += move

    def UndoMove(self, move_and_cost):
        # undoing a move is the same as doing a move in the inverse direction
        move, cost = move_and_cost
        self.State -= move      # the same as adding (move * -1) which is the inverse move

    def GenerateMoves(self):
        # simply check for boundaries and obstacles
        # the cost of all moves is 1 (diagonals could be 1.4 if they were legal)
        moves = []
        if self.State.real > 0 and not self.Grid[int((self.State.real - 1) * self.GridWidth + self.State.imag)]:
            moves.append( (-1, 1) )
        if self.State.real + 1 < self.GridHeight and not self.Grid[int((self.State.real + 1) * 
                                                                       self.GridWidth + self.State.imag)]:
            moves.append( (1, 1) )
        if self.State.imag > 0 and not self.Grid[int(self.State.real * 
                                                     self.GridWidth + self.State.imag - 1)]:
            moves.append( (-1j, 1) )
        if self.State.imag + 1 < self.GridWidth and not self.Grid[int(self.State.real * 
                                                                      self.GridWidth + self.State.imag + 1)]:
            moves.append( (1j, 1) )
        return moves

    def Solved(self):
        return self.State == self.Goal

    def Evaluate(self):
        # score can be the Manhattan distance between current state and goal state
        dist = self.Goal - self.State
        return int(abs(dist.real) + abs(dist.imag))
    

### Let's set up an interesting position see how things work

In [42]:
gw = GridWorld()
gw.SetStandardPosition()

The "standard" position is predefined, so that the problem is solvable, but not too easy. From the printout below you can see that the solution requires the character (marked as "X") to move around the obstacle in the middle and cannot go directly to the goal node (marked as "O"). Indeed, it needs to go through the narrow opening in the middle left part of the world.

NOTE. If you wish you can generate and use a random world by not setting the standard position above. But try 10x10 worlds first... gw = GridWorld(10, 10). Also check whether the generated world is actually solvable; it can happen that "X" and "O" are completely separated by obstacles as the world is randomly generated.

In [14]:
gw.PrintPosition()

||                     #########||
||#########   ###      ###      ||
||###    X    ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||


In [15]:
# Let's generate the moves in this position... it should be only left and right.
gw.GenerateMoves()

[((-0-1j), 1), (1j, 1)]

The mystic output means: there are two possible moves given as complex numbers (don't ask me why I programmed it like this -- I simply wanted to try complex numbers in python). So (-0-1j) means no change in row (real part), but -1j means move one step to the left (+1j is right). The move is a tuple ((-0-1j), 1), the second part (1) represents the cost of the move. In this domain all moves cost 1, but it can be changed. E.g., diagonals could be introduced which could cost square root of 2, so about 1.41.

In [18]:
# Let's do one move and see if the character obeys us.
gw.Move( (((-0-1j), 1)) )
gw.PrintPosition()

||                     #########||
||#########   ###      ###      ||
||### X       ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||


In [19]:
# Left the character went... by undoing the move we can get it back.
gw.UndoMove( (((-0-1j), 1)) )

In [20]:
# Has it reached the goal yet? Of course not.
gw.Solved()

False

### Let's use search to solve this problem

In [21]:
# A naively written library of search algorithm meant for demonstration only.
# I should rewrite it one day...
import bsearch

In [22]:
gw.PrintPosition()

||                     #########||
||#########   ###      ###      ||
||###    X    ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||


In [23]:
# First, let's run depth-first (DF) search as this is probably the simplest algorithm.
# However, don't forget that we want to supply it with a depth limit, otherwise...
# Well, otherwise it will find a cycle (there are plenty of them in this world) 
# and loop until the end of time...

# All the search algorithms take problem object as an argument. 
# DF additionally takes the depth limit.

# Perhaps give it a depth limit of 10 for starters.
solution = bsearch.DF(gw, 10)

In [25]:
print(solution)

None


None? Aha, no solution was found as the depth is too shalow. Okay, let's increase the depth to 20.

In [43]:
solution = bsearch.DF(gw, 20)
print(solution)

[((-0-1j), 1), (1, 1), (-1, 1), (1, 1), (-1, 1), (1, 1), (-1, 1), (1, 1), (1, 1), (1j, 1), (1, 1), (1, 1), (1, 1), (1, 1), (1j, 1), (1j, 1), (1j, 1), (-1, 1), (-1, 1), (-1, 1)]


In [27]:
# How long is the solution path?
len(solution)

20

Twenty moves? Yes, it's not a coincidence, it uses *all* the depth. If you read (or move) through the given solution, you'll notice that at first it cycles aimlessly around, but then goes straight for the goal. That's due to backtracking from the depth of twenty and trying alternatives on this path...

In [28]:
gw.PrintPosition()

||                     #########||
||#########   ###      ###      ||
||###    X    ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||


Note that the position of the world didn't change, the search neatly undid the moves all the way back to the starting position. If we want to apply the solution, we need to actually do the moves.

In [29]:
# There's an auxiliary method that does all the moves in a list it is given.
gw.ExecuteSequence(solution)

In [30]:
gw.Solved()

True

In [48]:
# And this method reverses all the moves in a given list.
gw.UndoSequence(solution)

In [49]:
# The following code shows the moves one by one by showing the current position after every move
print("Start")
gw.PrintPosition()
print()

for move in solution:
    print("Move:", move)
    gw.Move(move)
    gw.PrintPosition()
    print()

Start
||                     #########||
||#########   ###      ###      ||
||###    X    ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||

Move: ((-0-1j), 1)
||                     #########||
||#########   ###      ###      ||
||### X       ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||

Move: (1, 1)
||                     #########||
||#########   ###      ###      ||
||###         ###      ###   ###||
||    X ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         #

### Shall we find the optimal solution now?

In [52]:
# reset the world, starting fresh
gw = GridWorld()
gw.SetStandardPosition()

In [53]:
# Careful: this runs quite a bit longer (partly due to bad implementation of BF/world)
# not true anymore with the introduction of BF23 instead of BF 
# (it's still bad, but not nearly so bad!)

# Let's run breadth-first (BF) search!
# Since all the moves cost exactly one, the solution cost is measured in the number of moves.
# And BF finds the shallowest solution.

# BF23 stands for a bit better implementation in 2023. (deque used)
# You can run BF instead of BF23 
# to see the speed-up an optimised data structure gives, O(1) vs O(n) for .pop(0)

solBF = bsearch.BF23(gw)
# solBF = bsearch.BF(gw)   # <--- slow old version (yet it expands the same number of nodes)

In [38]:
len(solBF)

14

That's much better! The optimal solution is thus 14 moves long. We know it's optimal in the number of steps/moves due to how the BF algorithm works, remember from the lecture, right?

You can check the solution just like we did it above.

It did take much longer than DF search, but as pointed out previously, that's at least partly due to the bad implementation of BF. The real comparison is in the number of expanded nodes and that's what we should do next for all the algorithms.

### Comparing the algorithms in terms of space and time complexity

In [45]:
# Let's profile the algorithms.

# A profiler runs the code and counts the number of function calls and their execution time.
# This is exactly what we need, remember space complexity is connected with the number of
# generated nodes, and time complexity with the number of expanded nodes.

import cProfile

In [57]:
# reset the world, starting fresh again, just in case
gw = GridWorld()
gw.SetStandardPosition()
gw.PrintPosition()

||                     #########||
||#########   ###      ###      ||
||###    X    ###      ###   ###||
||      ###         ############||
||###            ######      ###||
||######   ###### O    ###      ||
||###         ###               ||
||###         ###               ||
||                              ||
||            ######            ||


In [51]:
cProfile.run("solDF = bsearch.DF(gw, 20)")

         620063 function calls (489074 primitive calls) in 0.464 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
   130989    0.041    0.000    0.041    0.000 <ipython-input-12-01f596e46ef9>:69(Move)
   130989    0.042    0.000    0.042    0.000 <ipython-input-12-01f596e46ef9>:73(UndoMove)
    48029    0.163    0.000    0.174    0.000 <ipython-input-12-01f596e46ef9>:78(GenerateMoves)
    48030    0.013    0.000    0.013    0.000 <ipython-input-12-01f596e46ef9>:95(Solved)
        1    0.000    0.000    0.463    0.463 <string>:1(<module>)
 130990/1    0.193    0.000    0.463    0.463 bsearch.py:9(DF)
        1    0.000    0.000    0.464    0.464 {built-in method builtins.exec}
   131013    0.012    0.000    0.012    0.000 {method 'append' of 'list' objects}
        1    0.000    0.000    0.000    0.000 {method 'disable' of '_lsprof.Profiler' objects}
       20    0.000    0.000    0.000    0.000 {method 'insert' of 'list' obj

What can we see from the profiler's output? 

The times, of course, but more importantly, the *number of calls* of each of the function/method. We will be more interested in the number of calls, because this is independent of the (bad) implementation and also the machine we're running the code on; including running something else in another window, slowing the computer down.

Remember, method Solved is only called when the search algorithm is *expanding* nodes. Thus, this will be our measure of performance (time complexity). Method GenerateMoves is called one time less for it's only called when Solved fails.

So now we know that DF with depth limit of 20 expanded 48,030 nodes!

In [59]:
# Now, let's compare with BF23 
# (run BF instead if you wish to check how a bad implementation affects performance)
# (the difference is only in time, not expanded nodes)

cProfile.run("solBF = bsearch.BF23(gw)")

         9294051 function calls in 4.661 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
   254424    0.615    0.000    1.315    0.000 <ipython-input-12-01f596e46ef9>:61(ExecuteSequence)
   254424    0.663    0.000    1.403    0.000 <ipython-input-12-01f596e46ef9>:65(UndoSequence)
  3196858    0.701    0.000    0.701    0.000 <ipython-input-12-01f596e46ef9>:69(Move)
  3196858    0.740    0.000    0.740    0.000 <ipython-input-12-01f596e46ef9>:73(UndoMove)
   254423    0.672    0.000    0.726    0.000 <ipython-input-12-01f596e46ef9>:78(GenerateMoves)
   254424    0.053    0.000    0.053    0.000 <ipython-input-12-01f596e46ef9>:95(Solved)
        1    0.023    0.023    4.661    4.661 <string>:1(<module>)
        1    0.100    0.100    4.638    4.638 bsearch.py:61(BF23)
   254424    0.960    0.000    4.538    0.000 bsearch.py:70(auxBF23)
        1    0.000    0.000    4.661    4.661 {built-in method builtins.exec}
   686894   

BF expands 254,424 nodes for this particular instance of the problem. So quite a bit more than DF. Is it worse than DF? No, this really depends on the domain and even a concrete instance of the problem. And remember, a simple DF without depth limit would cycle forever.

Now, how does the "best of both worlds", the iterative deepening (ID) algorithm perform? Remember, it returns the optimal solution just like BF, uses only linear amount of space, and doesn't need a depth limit given. It, in fact successively runs DF with increasing depth.

In [60]:
cProfile.run("solID = bsearch.ID(gw)")

         5226175 function calls (4126194 primitive calls) in 3.499 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
  1099981    0.311    0.000    0.311    0.000 <ipython-input-12-01f596e46ef9>:69(Move)
  1099981    0.314    0.000    0.314    0.000 <ipython-input-12-01f596e46ef9>:73(UndoMove)
   413101    1.235    0.000    1.324    0.000 <ipython-input-12-01f596e46ef9>:78(GenerateMoves)
   413102    0.103    0.000    0.103    0.000 <ipython-input-12-01f596e46ef9>:95(Solved)
        1    0.000    0.000    3.499    3.499 <string>:1(<module>)
        1    0.000    0.000    3.499    3.499 bsearch.py:22(ID)
1099996/15    1.447    0.000    3.499    0.233 bsearch.py:9(DF)
        1    0.000    0.000    3.499    3.499 {built-in method builtins.exec}
  1099996    0.089    0.000    0.089    0.000 {method 'append' of 'list' objects}
        1    0.000    0.000    0.000    0.000 {method 'disable' of '_lsprof.Profiler' objects}
       14

Huh, it's faster timewise than BF? Not what theory says, right? Yes, this is due to bad implementation of BF (and also BF23, trust me).

Again, the number of expanded nodes is the real measure of time complexity. And it expands 413,102 nodes. Remember the theory about how much extra work ID does compared to BF? Yes, b/(b-1), where b stands for the branching factor.

This is just one example (we should try on several more starting positions / problem instances), but let's compare nevertheless. So, 413,102 / 254,424 is...

In [61]:
413102 / 254424

1.6236754394239536

If we assume the average branching factor for these problems is about 3, that puts the estimate for the overhead at about 3/(3-1) = 1.5 --- quite comparable to 1.62 above, right? Knowing theory can be helpful! ;)

In [62]:
len(solID)

14

No surprises here, ID, of course, finds the shortest path as it gradually increases the search depth of the underlying DF search by 1.

### Heuristics makes it fast, right?

Well, provided it's a good heuristic ;)

For these problems, we'll use the Manhattan distance between "X" and "O" as our heuristic evaluation. It's simply calculated as the difference in X plus the difference in Y-coordinate (see Evaluate method). It also has the benefit that it's *admissible* (never overestimates the solution cost), so using it with A* or IDA* (and some other algorithms we didn't cover) *guarantees* an optimal solution in terms of solution cost (here it's the same as the number of moves).

In [63]:
cProfile.run("solA = bsearch.A(gw)")

         1507 function calls in 0.006 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
       97    0.000    0.000    0.000    0.000 <ipython-input-12-01f596e46ef9>:40(ID)
       37    0.000    0.000    0.000    0.000 <ipython-input-12-01f596e46ef9>:61(ExecuteSequence)
       37    0.000    0.000    0.000    0.000 <ipython-input-12-01f596e46ef9>:65(UndoSequence)
      303    0.000    0.000    0.000    0.000 <ipython-input-12-01f596e46ef9>:69(Move)
      303    0.000    0.000    0.000    0.000 <ipython-input-12-01f596e46ef9>:73(UndoMove)
       36    0.001    0.000    0.001    0.000 <ipython-input-12-01f596e46ef9>:78(GenerateMoves)
       37    0.000    0.000    0.000    0.000 <ipython-input-12-01f596e46ef9>:95(Solved)
       45    0.001    0.000    0.001    0.000 <ipython-input-12-01f596e46ef9>:98(Evaluate)
        1    0.001    0.001    0.005    0.005 <string>:1(<module>)
       37    0.001    0.000    0.003    0.000 bsearc

Well... that *is* fast! Only 37 expanded nodes! Orders of magnitude faster than all the uninformed search algorithms above. Even with quite bad implementation of A* (trust me, I didn't do a good job with it, it's for demonstration purposes only). The speed-up comes from the "artificial reduction" of the branching factor, b' << b, due to the guidance from the heuristic function.

That is the power of good heuristics and the so-called informed search algorithms. Let's also check the solution length for optimality --- remember, it should be optimal as the Manhattan distance for this problem is provably admissible.

In [64]:
len(solA)

14

Theory holds, all good. You can check it with other instances of the GridWorld and it should always be optimal. Compare it against the slower BF and ID if in doubt with your manual solution.

In [65]:
cProfile.run("solIDA = bsearch.IDA(gw)")

         128442 function calls (111999 primitive calls) in 0.156 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
    16443    0.008    0.000    0.008    0.000 <ipython-input-12-01f596e46ef9>:69(Move)
    16443    0.008    0.000    0.008    0.000 <ipython-input-12-01f596e46ef9>:73(UndoMove)
     6642    0.033    0.000    0.035    0.000 <ipython-input-12-01f596e46ef9>:78(GenerateMoves)
     6643    0.002    0.000    0.002    0.000 <ipython-input-12-01f596e46ef9>:95(Solved)
    16449    0.018    0.000    0.022    0.000 <ipython-input-12-01f596e46ef9>:98(Evaluate)
        1    0.000    0.000    0.132    0.132 <string>:1(<module>)
        1    0.000    0.000    0.132    0.132 bsearch.py:137(IDA)
  16448/5    0.057    0.000    0.132    0.026 bsearch.py:147(rIDA)
    32898    0.004    0.000    0.004    0.000 {built-in method builtins.abs}
        1    0.024    0.024    0.156    0.156 {built-in method builtins.exec}
    16458    0.

IDA* is fast, but not nearly as fast as A* . It expands 6,643 nodes. However, it's super space-efficient using only linear space. Remember, IDA* works best when many nodes share the same f-scores (nevertheless A* is faster, of course)...